# Optimising SQL Queries
© Explore Data Science Academy

## Learning Objectives

In this train, you will learn:
- Common Table Expressions,
- How to optimise SQL queries, and
- How to measure the execution time of a block of code in Jupyter.


## Outline

In this train, we'll go through the following: 
- Why optimise queries?
- Common Table Expressions (CTEs).
- Write efficient SQL queries:
    - Column names instead of *
    - Create JOINS with INNER, not WHERE
    - Avoid using the wildcard (%) at the beginning of a predicate
    - Avoid using functions in predicates
    - Avoid using calculated fields in the JOIN and WHERE clauses

## US Flights Database
In this train, we'll be using the US Flights database with actual US flights data to illustrate the optimisation techniques with large amounts of data. We will also use iPython's built-in `%%time` magic command which will measure the execution time of code within a given jupyter cell. To follow along, you will need to download the `flights.db` database file from Athena. The flights database consist of the following tables:

- **flights**:     all domestic flights in the USA in 2008
- **carriers**:     lookup table for all the carriers
- **airports**:     lookup table for all the airports
- **planes**:     lookup table for the planes

For your convenience, we have also provided the flights database ER diagram:



<img src="https://raw.githubusercontent.com/Explore-AI/Pictures/master/flights_db_ER.png" width=30% align="left">

Loading SQL magics and load database:

In [1]:
%load_ext sql

# Load SQLite database 
# Make sure this file is in the same directory as your notebook
%sql sqlite:///flights.db 

## Why optimise queries?

Depending on the size of the database and the nature of the query, SQL queries can take a long time to run. Also, writing SQL massive queries can potentially clog a server (in a server-based setup). For example, if a server spends too long on a single query then other queries need to "wait in line" for the server to finish processing the one query. As such, it is important that we write more efficient queries. For example, queries that read as much data as is necessary.

## Common Table Expressions (CTEs)

A CTE is a temporary result (i.e. not saved in the database) set that you can reference within a larger query. A CTE is useful in cases where we need to write nested queries and complex joins. CTEs can be recursive or non-recursive and can be better than standard nested queries when:

- The result of the outer query is referenced more than once.
- Writing recursive queries.

### Non-recursive CTE syntax

A non-recursive CTE can be created as follows:

```SQL
WITH CTE AS
(
SELECT Column1, Column2
FROM table1
)
```
and used as follows:

```SQL
SELECT Column1 
FROM CTE
```

**Note:** For clarity of display, we've cleaned the output of all queries. Please re-run these locally or on Google Colab to see their full output. 

## Column names instead of *
**Scenario:** We are only interested in the tail number and delay before departure for each flight. 
 
### Inefficient query

In [5]:
%%time
%%sql

SELECT * 
FROM flights
LIMIT 2500

 * sqlite:///flights.db
Done.
Wall time: 79.9 ms


[(0, '2008/1/3', 4, 2003.0, '1955', 2211.0, '2225', 'WN', '335', 'N712SW', 128.0, '150', '116.0', -14.0, 8.0, 'IAD', 'TPA', 810, '4', '8', '0', None, '0', None, None, None, None, None),
 (1, '2008/1/3', 4, 754.0, '735', 1002.0, '1000', 'WN', '3231', 'N772SW', 128.0, '145', '113.0', 2.0, 19.0, 'IAD', 'TPA', 810, '5', '10', '0', None, '0', None, None, None, None, None),
 (2, '2008/1/3', 4, 628.0, '620', 804.0, '750', 'WN', '448', 'N428WN', 96.0, '90', '76.0', 14.0, 8.0, 'IND', 'BWI', 515, '3', '17', '0', None, '0', None, None, None, None, None),
 (3, '2008/1/3', 4, 926.0, '930', 1054.0, '1100', 'WN', '1746', 'N612SW', 88.0, '90', '78.0', -6.0, -4.0, 'IND', 'BWI', 515, '3', '7', '0', None, '0', None, None, None, None, None),
 (4, '2008/1/3', 4, 1829.0, '1755', 1959.0, '1925', 'WN', '3920', 'N464WN', 90.0, '90', '77.0', 34.0, 34.0, 'IND', 'BWI', 515, '3', '10', '0', None, '0', '2', '0', '0', '0', '32'),
 (5, '2008/1/3', 4, 1940.0, '1915', 2121.0, '2110', 'WN', '378', 'N726SW', 101.0, '115', '87.0', 11.0, 25.0, 'IND', 'JAX', 688, '4', '10', '0', None, '0', None, None, None, None, None),
 (6, '2008/1/3', 4, 1937.0, '1830', 2037.0, '1940', 'WN', '509', 'N763SW', 240.0, '250', '230.0', 57.0, 67.0, 'IND', 'LAS', 1591, '3', '7', '0', None, '0', '10', '0', '0', '0', '47'),
 (7, '2008/1/3', 4, 1039.0, '1040', 1132.0, '1150', 'WN', '535', 'N428WN', 233.0, '250', '219.0', -18.0, -1.0, 'IND', 'LAS', 1591, '7', '7', '0', None, '0', None, None, None, None, None),
 (8, '2008/1/3', 4, 617.0, '615', 652.0, '650', 'WN', '11', 'N689SW', 95.0, '95', '70.0', 2.0, 2.0, 'IND', 'MCI', 451, '6', '19', '0', None, '0', None, None, None, None, None),
 (9, '2008/1/3', 4, 1620.0, '1620', 1639.0, '1655', 'WN', '810', 'N648SW', 79.0, '95', '70.0', -16.0, 0.0, 'IND', 'MCI', 451, '3', '6', '0', None, '0', None, None, None, None, None),
 (10, '2008/1/3', 4, 706.0, '700', 916.0, '915', 'WN', '100', 'N690SW', 130.0, '135', '106.0', 1.0, 6.0, 'IND', 'MCO', 828, '5', '19', '0', None, '0', None, None, None, None, None),
 (11, '2008/1/3', 4, 1644.0, '1510', 1845.0, '1725', 'WN', '1333', 'N334SW', 121.0, '135', '107.0', 80.0, 94.0, 'IND', 'MCO', 828, '6', '8', '0', None, '0', '8', '0', '0', '0', '72'),
 (12, '2008/1/3', 4, 1426.0, '1430', 1426.0, '1425', 'WN', '829', 'N476WN', 60.0, '55', '39.0', 1.0, -4.0, 'IND', 'MDW', 162, '9', '12', '0', None, '0', None, None, None, None, None),
 (13, '2008/1/3', 4, 715.0, '715', 720.0, '710', 'WN', '1016', 'N765SW', 65.0, '55', '37.0', 10.0, 0.0, 'IND', 'MDW', 162, '7', '21', '0', None, '0', None, None, None, None, None),
 (14, '2008/1/3', 4, 1702.0, '1700', 1651.0, '1655', 'WN', '1827', 'N420WN', 49.0, '55', '35.0', -4.0, 2.0, 'IND', 'MDW', 162, '4', '10', '0', None, '0', None, None, None, None, None),
 (15, '2008/1/3', 4, 1029.0, '1020', 1021.0, '1010', 'WN', '2272', 'N263WN', 52.0, '50', '37.0', 11.0, 9.0, 'IND', 'MDW', 162, '6', '9', '0', None, '0', None, None, None, None, None),
 (16, '2008/1/3', 4, 1452.0, '1425', 1640.0, '1625', 'WN', '675', 'N286WN', 228.0, '240', '213.0', 15.0, 27.0, 'IND', 'PHX', 1489, '7', '8', '0', None, '0', '3', '0', '0', '0', '12'),
 (17, '2008/1/3', 4, 754.0, '745', 940.0, '955', 'WN', '1144', 'N778SW', 226.0, '250', '205.0', -15.0, 9.0, 'IND', 'PHX', 1489, '5', '16', '0', None, '0', None, None, None, None, None),
 (18, '2008/1/3', 4, 1323.0, '1255', 1526.0, '1510', 'WN', '4', 'N674AA', 123.0, '135', '110.0', 16.0, 28.0, 'IND', 'TPA', 838, '4', '9', '0', None, '0', '0', '0', '0', '0', '16'),
 (19, '2008/1/3', 4, 1416.0, '1325', 1512.0, '1435', 'WN', '54', 'N643SW', 56.0, '70', '49.0', 37.0, 51.0, 'ISP', 'BWI', 220, '2', '5', '0', None, '0', '12', '0', '0', '0', '25'),
 (20, '2008/1/3', 4, 706.0, '705', 807.0, '810', 'WN', '68', 'N497WN', 61.0, '65', '51.0', -3.0, 1.0, 'ISP', 'BWI', 220, '3', '7', '0', None, '0', None, None, None, None, None),
 (21, '2008/1/3', 4, 1657.0, '1625', 1754.0, '1735', 'WN', '623', 'N724SW', 57.0, '70', '47.0', 19.0, 32.0, 'ISP', 'BWI', 220, '5', '5', '0', None, '0', '7', '0

### Efficient query

In [3]:
%%time
%%sql

SELECT TailNum, DepDelay 
FROM flights 
LIMIT 2500

 * sqlite:///flights.db
Done.
Wall time: 20 ms


[('N712SW', 8.0),
 ('N772SW', 19.0),
 ('N428WN', 8.0),
 ('N612SW', -4.0),
 ('N464WN', 34.0),
 ('N726SW', 25.0),
 ('N763SW', 67.0),
 ('N428WN', -1.0),
 ('N689SW', 2.0),
 ('N648SW', 0.0),
 ('N690SW', 6.0),
 ('N334SW', 94.0),
 ('N476WN', -4.0),
 ('N765SW', 0.0),
 ('N420WN', 2.0),
 ('N263WN', 9.0),
 ('N286WN', 27.0),
 ('N778SW', 9.0),
 ('N674AA', 28.0),
 ('N643SW', 51.0),
 ('N497WN', 1.0),
 ('N724SW', 32.0),
 ('N786SW', 20.0),
 ('N714CB', 9.0),
 ('N222WN', 1.0),
 ('N394SW', 25.0),
 ('N215WN', 87.0),
 ('N243WN', 29.0),
 ('N454WN', 1.0),
 ('N712SW', 4.0),
 ('N798SW', 82.0),
 ('N736SA', 3.0),
 ('N795SW', 2.0),
 ('N247WN', 12.0),
 ('N707SA', 19.0),
 ('N443WN', 39.0),
 ('N753SW', 1.0),
 ('N779SW', 82.0),
 ('N704SW', 22.0),
 ('N709SW', 29.0),
 ('N459WN', 56.0),
 ('N621SW', 24.0),
 ('N206WN', 6.0),
 ('N280WN', 6.0),
 ('N241WN', 13.0),
 ('N200WN', 18.0),
 ('N459WN', -1.0),
 ('N286WN', 1.0),
 ('N475WN', 15.0),
 ('N792SW', 315.0),
 ('N202WN', 0.0),
 ('N646SW', 5.0),
 ('N252WN', 45.0),
 ('N346SW', 53.0),
 ('N299WN', 10.0),
 ('N528SW', 0.0),
 ('N487WN', 23.0),
 ('N243WN', 26.0),
 ('N479WN', 30.0),
 ('N255WN', 0.0),
 ('N215WN', 4.0),
 ('N264LV', -2.0),
 ('N714CB', -7.0),
 ('N436WN', 5.0),
 ('N726SW', 9.0),
 ('N399WN', 0.0),
 ('N387SW', 0.0),
 ('N405WN', 1.0),
 ('N685SW', 1.0),
 ('N467WN', 8.0),
 ('N643SW', 38.0),
 ('N263WN', 12.0),
 ('N363SW', -5.0),
 ('N257WN', 1.0),
 ('N521SW', 44.0),
 ('N663SW', 12.0),
 ('N376SW', 8.0),
 ('N791SW', 58.0),
 ('N392SW', 9.0),
 ('N799SW', 53.0),
 ('N607SW', -2.0),
 ('N618WN', 83.0),
 ('N682SW', 57.0),
 ('N456WN', -1.0),
 ('N509SW', 14.0),
 ('N293', 2.0),
 ('N473WN', 97.0),
 ('N351SW', 34.0),
 ('N238WN', 16.0),
 ('N499WN', 63.0),
 ('N309SW', 15.0),
 ('N245WN', 59.0),
 ('N467WN', 1.0),
 ('N256WN', 1.0),
 ('N275WN', 45.0),
 ('N271WN', 26.0),
 ('N434WN', 69.0),
 ('N312SW', 4.0),
 ('N619SW', 36.0),
 ('N290WN', 69.0),
 ('N493WN', 1.0),
 ('N383SW', 63.0),
 ('N608SW', 38.0),
 ('N777QC', 0.0),
 ('N626SW', 51.0),
 ('N369SW', 211.0),
 ('N396SW', 14.0),
 ('N293', 10.0),
 ('N509SW', 16.0),
 ('N409WN', 56.0),
 ('N278WN', 0.0),
 ('N695SW', 9.0),
 ('N284WN', 4.0),
 ('N220WN', 23.0),
 ('N784SW', 47.0),
 ('N463WN', 3.0),
 ('N244WN', 11.0),
 ('N455WN', 69.0),
 ('N297WN', 10.0),
 ('N688SW', 1.0),
 ('N481WN', 17.0),
 ('N203WN', 77.0),
 ('N491WN', 117.0),
 ('N480WN', 30.0),
 ('N318SW', 14.0),
 ('N647SW', 27.0),
 ('N313SW', 35.0),
 ('N352SW', 9.0),
 ('N321SW', 27.0),
 ('N660SW', 65.0),
 ('N414WN', 49.0),
 ('N408WN', 10.0),
 ('N475WN', 9.0),
 ('N321SW', 41.0),
 ('N230WN', 30.0),
 ('N761RR', 275.0),
 ('N464WN', 39.0),
 ('N272WN', 52.0),
 ('N499WN', 23.0),
 ('N244WN', 17.0),
 ('N335SW', 26.0),
 ('N488WN', 16.0),
 ('N496WN', 61.0),
 ('N401WN', 4.0),
 ('N351SW', 0.0),
 ('N422WN', 15.0),
 ('N288WN', 0.0),
 ('N792SW', 28.0),
 ('N352SW', 42.0),
 ('N335SW', 38.0),
 ('N465WN', 3.0),
 ('N609SW', 3.0),
 ('N404WN', 47.0),
 ('N787SA', 9.0),
 ('N617SW', 30.0),
 ('N302SW', 16.0),
 ('N763SW', 73.0),
 ('N676SW', 58.0),
 ('N775SW', 72.0),
 ('N634SW', -2.0),
 ('N449WN', 23.0),
 ('N444WN', 19.0),
 ('N764SW', 6.0),
 ('N723SW', 3.0),
 ('N712SW', 2.0),
 ('N407WN', 9.0),
 ('N232WN', 26.0),
 ('N725SW', 19.0),
 ('N436WN', -1.0),
 ('N745SW', 8.0),
 ('N740SW', 34.0),
 ('N405WN', 90.0),
 ('N468WN', 87.0),
 ('N201LV', 44.0),
 ('N222WN', 18.0),
 ('N295WN', 0.0),
 ('N282WN', 38.0),
 ('N782SA', -2.0),
 (None, None),
 ('N784SW', 9.0),
 ('N223WN', 124.0),
 ('N281WN', 46.0),
 ('N460WN', 43.0),
 ('N640SW', 1.0),
 ('N679AA', 51.0),
 ('N378SW', 70.0),
 ('N248WN', 13.0),
 ('N774SW', 10.0),
 ('N408WN', 1.0),
 ('N695SW', 15.0),
 ('N354SW', 2.0),
 ('N627SW', 7.0),
 ('N622SW', 80.0),
 ('N217JC', 89.0),
 ('N673AA', 3.0),
 ('N690SW', 3.0),
 ('N259WN', 30.0),
 ('N244WN', 0.0),
 ('N788SA', 3.0),
 ('N301SW', 32.0),
 ('N356SW', 58.0),
 ('N742SW', 16.0),
 ('N313SW', 15.0),
 ('N273WN', 38.0),
 ('N660SW', 28.0),
 ('N466WN', 62.0),
 ('N678AA', 21.0),
 ('N484WN', 0.0),
 ('N258WN', 33.0),
 ('N608SW', 54.0),
 ('N435WN', 42.0),
 ('N484WN', 20.0),
 ('N639SW', -1.0),
 ('N228WN', 7.0),
 ('N747S

### Why it’s more efficient
Many SQL developers use SELECT * FROM table to get look at column data which becomes taxing if there are many records (normally a few million or more).

Returning only the required columns reduces the total data being read and subsequently runtime. When using * (i.e. want all columns), it’s important to then limit the number of rows using `LIMIT X`


## Create JOINS with INNER, not WHERE
**Scenario:** We want the carrier description to be added to the flights table.
 
### Inefficient query

In [8]:
%%time
%%sql

SELECT FlightNum, TailNum, Description
FROM flights, carriers
WHERE carriers.Code = flights.UniqueCarrier
LIMIT 2500;

 * sqlite:///flights.db
Done.
Wall time: 32 ms


[('335', 'N712SW', 'Southwest Airlines Co.\r'),
 ('3231', 'N772SW', 'Southwest Airlines Co.\r'),
 ('448', 'N428WN', 'Southwest Airlines Co.\r'),
 ('1746', 'N612SW', 'Southwest Airlines Co.\r'),
 ('3920', 'N464WN', 'Southwest Airlines Co.\r'),
 ('378', 'N726SW', 'Southwest Airlines Co.\r'),
 ('509', 'N763SW', 'Southwest Airlines Co.\r'),
 ('535', 'N428WN', 'Southwest Airlines Co.\r'),
 ('11', 'N689SW', 'Southwest Airlines Co.\r'),
 ('810', 'N648SW', 'Southwest Airlines Co.\r'),
 ('100', 'N690SW', 'Southwest Airlines Co.\r'),
 ('1333', 'N334SW', 'Southwest Airlines Co.\r'),
 ('829', 'N476WN', 'Southwest Airlines Co.\r'),
 ('1016', 'N765SW', 'Southwest Airlines Co.\r'),
 ('1827', 'N420WN', 'Southwest Airlines Co.\r'),
 ('2272', 'N263WN', 'Southwest Airlines Co.\r'),
 ('675', 'N286WN', 'Southwest Airlines Co.\r'),
 ('1144', 'N778SW', 'Southwest Airlines Co.\r'),
 ('4', 'N674AA', 'Southwest Airlines Co.\r'),
 ('54', 'N643SW', 'Southwest Airlines Co.\r'),
 ('68', 'N497WN', 'Southwest Airlines Co.\r'),
 ('623', 'N724SW', 'Southwest Airlines Co.\r'),
 ('717', 'N786SW', 'Southwest Airlines Co.\r'),
 ('1244', 'N714CB', 'Southwest Airlines Co.\r'),
 ('2101', 'N222WN', 'Southwest Airlines Co.\r'),
 ('2553', 'N394SW', 'Southwest Airlines Co.\r'),
 ('188', 'N215WN', 'Southwest Airlines Co.\r'),
 ('1754', 'N243WN', 'Southwest Airlines Co.\r'),
 ('2275', 'N454WN', 'Southwest Airlines Co.\r'),
 ('550', 'N712SW', 'Southwest Airlines Co.\r'),
 ('362', 'N798SW', 'Southwest Airlines Co.\r'),
 ('543', 'N736SA', 'Southwest Airlines Co.\r'),
 ('1112', 'N795SW', 'Southwest Airlines Co.\r'),
 ('1397', 'N247WN', 'Southwest Airlines Co.\r'),
 ('3398', 'N707SA', 'Southwest Airlines Co.\r'),
 ('3480', 'N443WN', 'Southwest Airlines Co.\r'),
 ('300', 'N753SW', 'Southwest Airlines Co.\r'),
 ('422', 'N779SW', 'Southwest Airlines Co.\r'),
 ('1837', 'N704SW', 'Southwest Airlines Co.\r'),
 ('2871', 'N709SW', 'Southwest Airlines Co.\r'),
 ('1056', 'N459WN', 'Southwest Airlines Co.\r'),
 ('2175', 'N621SW', 'Southwest Airlines Co.\r'),
 ('3319', 'N206WN', 'Southwest Airlines Co.\r'),
 ('3667', 'N280WN', 'Southwest Airlines Co.\r'),
 ('2006', 'N241WN', 'Southwest Airlines Co.\r'),
 ('3858', 'N200WN', 'Southwest Airlines Co.\r'),
 ('3928', 'N459WN', 'Southwest Airlines Co.\r'),
 ('534', 'N286WN', 'Southwest Airlines Co.\r'),
 ('3244', 'N475WN', 'Southwest Airlines Co.\r'),
 ('186', 'N792SW', 'Southwest Airlines Co.\r'),
 ('971', 'N202WN', 'Southwest Airlines Co.\r'),
 ('2124', 'N646SW', 'Southwest Airlines Co.\r'),
 ('3154', 'N252WN', 'Southwest Airlines Co.\r'),
 ('1035', 'N346SW', 'Southwest Airlines Co.\r'),
 ('205', 'N299WN', 'Southwest Airlines Co.\r'),
 ('449', 'N528SW', 'Southwest Airlines Co.\r'),
 ('3430', 'N487WN', 'Southwest Airlines Co.\r'),
 ('1580', 'N243WN', 'Southwest Airlines Co.\r'),
 ('2195', 'N479WN', 'Southwest Airlines Co.\r'),
 ('2804', 'N255WN', 'Southwest Airlines Co.\r'),
 ('3428', 'N215WN', 'Southwest Airlines Co.\r'),
 ('433', 'N264LV', 'Southwest Airlines Co.\r'),
 ('1331', 'N714CB', 'Southwest Airlines Co.\r'),
 ('3504', 'N436WN', 'Southwest Airlines Co.\r'),
 ('378', 'N726SW', 'Southwest Airlines Co.\r'),
 ('640', 'N399WN', 'Southwest Airlines Co.\r'),
 ('1396', 'N387SW', 'Southwest Airlines Co.\r'),
 ('2189', 'N405WN', 'Southwest Airlines Co.\r'),
 ('3312', 'N685SW', 'Southwest Airlines Co.\r'),
 ('3948', 'N467WN', 'Southwest Airlines Co.\r'),
 ('54', 'N643SW', 'Southwest Airlines Co.\r'),
 ('2272', 'N263WN', 'Southwest Airlines Co.\r'),
 ('549', 'N363SW', 'Southwest Airlines Co.\r'),
 ('3604', 'N257WN', 'Southwest Airlines Co.\r'),
 ('23', 'N521SW', 'Southwest Airlines Co.\r'),
 ('1232', 'N663SW', 'Southwest Airlines Co.\r'),
 ('977', 'N376SW', 'Southwest Airlines Co.\r'),
 ('1574', 'N791SW', 'Southwest Airlines Co.\r'),
 ('2019', 'N392SW', 'Southwest Airlines Co.\r'),
 ('500', 'N799SW', 'Southwest Airlines Co.\r'),
 ('778', 'N607SW', 'Southwest Airlines Co.\r'),
 ('890', 'N618WN', 'Southwest Airlines Co.\r'),
 ('1171', 'N682SW', 'Sout

### Efficient query

In [9]:
%%time
%%sql

SELECT FlightNum, TailNum, Description
FROM flights
INNER JOIN carriers
ON carriers.Code = flights.UniqueCarrier
LIMIT 2500;

 * sqlite:///flights.db
Done.
Wall time: 41 ms


[('335', 'N712SW', 'Southwest Airlines Co.\r'),
 ('3231', 'N772SW', 'Southwest Airlines Co.\r'),
 ('448', 'N428WN', 'Southwest Airlines Co.\r'),
 ('1746', 'N612SW', 'Southwest Airlines Co.\r'),
 ('3920', 'N464WN', 'Southwest Airlines Co.\r'),
 ('378', 'N726SW', 'Southwest Airlines Co.\r'),
 ('509', 'N763SW', 'Southwest Airlines Co.\r'),
 ('535', 'N428WN', 'Southwest Airlines Co.\r'),
 ('11', 'N689SW', 'Southwest Airlines Co.\r'),
 ('810', 'N648SW', 'Southwest Airlines Co.\r'),
 ('100', 'N690SW', 'Southwest Airlines Co.\r'),
 ('1333', 'N334SW', 'Southwest Airlines Co.\r'),
 ('829', 'N476WN', 'Southwest Airlines Co.\r'),
 ('1016', 'N765SW', 'Southwest Airlines Co.\r'),
 ('1827', 'N420WN', 'Southwest Airlines Co.\r'),
 ('2272', 'N263WN', 'Southwest Airlines Co.\r'),
 ('675', 'N286WN', 'Southwest Airlines Co.\r'),
 ('1144', 'N778SW', 'Southwest Airlines Co.\r'),
 ('4', 'N674AA', 'Southwest Airlines Co.\r'),
 ('54', 'N643SW', 'Southwest Airlines Co.\r'),
 ('68', 'N497WN', 'Southwest Airlines Co.\r'),
 ('623', 'N724SW', 'Southwest Airlines Co.\r'),
 ('717', 'N786SW', 'Southwest Airlines Co.\r'),
 ('1244', 'N714CB', 'Southwest Airlines Co.\r'),
 ('2101', 'N222WN', 'Southwest Airlines Co.\r'),
 ('2553', 'N394SW', 'Southwest Airlines Co.\r'),
 ('188', 'N215WN', 'Southwest Airlines Co.\r'),
 ('1754', 'N243WN', 'Southwest Airlines Co.\r'),
 ('2275', 'N454WN', 'Southwest Airlines Co.\r'),
 ('550', 'N712SW', 'Southwest Airlines Co.\r'),
 ('362', 'N798SW', 'Southwest Airlines Co.\r'),
 ('543', 'N736SA', 'Southwest Airlines Co.\r'),
 ('1112', 'N795SW', 'Southwest Airlines Co.\r'),
 ('1397', 'N247WN', 'Southwest Airlines Co.\r'),
 ('3398', 'N707SA', 'Southwest Airlines Co.\r'),
 ('3480', 'N443WN', 'Southwest Airlines Co.\r'),
 ('300', 'N753SW', 'Southwest Airlines Co.\r'),
 ('422', 'N779SW', 'Southwest Airlines Co.\r'),
 ('1837', 'N704SW', 'Southwest Airlines Co.\r'),
 ('2871', 'N709SW', 'Southwest Airlines Co.\r'),
 ('1056', 'N459WN', 'Southwest Airlines Co.\r'),
 ('2175', 'N621SW', 'Southwest Airlines Co.\r'),
 ('3319', 'N206WN', 'Southwest Airlines Co.\r'),
 ('3667', 'N280WN', 'Southwest Airlines Co.\r'),
 ('2006', 'N241WN', 'Southwest Airlines Co.\r'),
 ('3858', 'N200WN', 'Southwest Airlines Co.\r'),
 ('3928', 'N459WN', 'Southwest Airlines Co.\r'),
 ('534', 'N286WN', 'Southwest Airlines Co.\r'),
 ('3244', 'N475WN', 'Southwest Airlines Co.\r'),
 ('186', 'N792SW', 'Southwest Airlines Co.\r'),
 ('971', 'N202WN', 'Southwest Airlines Co.\r'),
 ('2124', 'N646SW', 'Southwest Airlines Co.\r'),
 ('3154', 'N252WN', 'Southwest Airlines Co.\r'),
 ('1035', 'N346SW', 'Southwest Airlines Co.\r'),
 ('205', 'N299WN', 'Southwest Airlines Co.\r'),
 ('449', 'N528SW', 'Southwest Airlines Co.\r'),
 ('3430', 'N487WN', 'Southwest Airlines Co.\r'),
 ('1580', 'N243WN', 'Southwest Airlines Co.\r'),
 ('2195', 'N479WN', 'Southwest Airlines Co.\r'),
 ('2804', 'N255WN', 'Southwest Airlines Co.\r'),
 ('3428', 'N215WN', 'Southwest Airlines Co.\r'),
 ('433', 'N264LV', 'Southwest Airlines Co.\r'),
 ('1331', 'N714CB', 'Southwest Airlines Co.\r'),
 ('3504', 'N436WN', 'Southwest Airlines Co.\r'),
 ('378', 'N726SW', 'Southwest Airlines Co.\r'),
 ('640', 'N399WN', 'Southwest Airlines Co.\r'),
 ('1396', 'N387SW', 'Southwest Airlines Co.\r'),
 ('2189', 'N405WN', 'Southwest Airlines Co.\r'),
 ('3312', 'N685SW', 'Southwest Airlines Co.\r'),
 ('3948', 'N467WN', 'Southwest Airlines Co.\r'),
 ('54', 'N643SW', 'Southwest Airlines Co.\r'),
 ('2272', 'N263WN', 'Southwest Airlines Co.\r'),
 ('549', 'N363SW', 'Southwest Airlines Co.\r'),
 ('3604', 'N257WN', 'Southwest Airlines Co.\r'),
 ('23', 'N521SW', 'Southwest Airlines Co.\r'),
 ('1232', 'N663SW', 'Southwest Airlines Co.\r'),
 ('977', 'N376SW', 'Southwest Airlines Co.\r'),
 ('1574', 'N791SW', 'Southwest Airlines Co.\r'),
 ('2019', 'N392SW', 'Southwest Airlines Co.\r'),
 ('500', 'N799SW', 'Southwest Airlines Co.\r'),
 ('778', 'N607SW', 'Southwest Airlines Co.\r'),
 ('890', 'N618WN', 'Southwest Airlines Co.\r'),
 ('1171', 'N682SW', 'Sout

### Why it’s more efficient
Joining tables using the WHERE clause is similar to doing a CROSS join. This type of join will first generate all possible combinations of the values in the joining columns and then filter these results according to the specified condition, this means we iterate through the combination of records from both tables. However, when a join operation is performed, only records in the left table are iterated through to find matches in right table. 

## Avoid using the wildcard (%) at the beginning of a predicate
**Scenario:** We want the tail number and distance of all flights whose tail number starts with ‘N7’ 
 
### Inefficient query

In [10]:
%%time
%%sql

SELECT TailNum, Distance
FROM flights
WHERE TailNum LIKE '%N7%'
LIMIT 2500;

 * sqlite:///flights.db
Done.
Wall time: 85 ms


[('N712SW', 810),
 ('N772SW', 810),
 ('N726SW', 688),
 ('N763SW', 1591),
 ('N765SW', 162),
 ('N778SW', 1489),
 ('N724SW', 220),
 ('N786SW', 220),
 ('N714CB', 220),
 ('N712SW', 2283),
 ('N798SW', 972),
 ('N736SA', 972),
 ('N795SW', 972),
 ('N707SA', 972),
 ('N753SW', 765),
 ('N779SW', 765),
 ('N704SW', 765),
 ('N709SW', 765),
 ('N792SW', 359),
 ('N714CB', 663),
 ('N726SW', 318),
 ('N791SW', 180),
 ('N799SW', 487),
 ('N777QC', 223),
 ('N784SW', 2106),
 ('N761RR', 1591),
 ('N792SW', 236),
 ('N787SA', 1295),
 ('N763SW', 1140),
 ('N775SW', 1140),
 ('N764SW', 1521),
 ('N723SW', 1521),
 ('N712SW', 1521),
 ('N725SW', 1521),
 ('N745SW', 1521),
 ('N740SW', 1521),
 ('N782SA', 407),
 ('N784SW', 407),
 ('N774SW', 407),
 ('N788SA', 197),
 ('N742SW', 197),
 ('N747SA', 256),
 ('N777QC', 256),
 ('N752SW', 256),
 ('N790SW', 256),
 ('N794SW', 1910),
 ('N715SW', 1910),
 ('N734SA', 258),
 ('N794SW', 1069),
 ('N768SW', 1624),
 ('N731SA', 866),
 ('N776WN', 386),
 ('N756SA', 368),
 ('N766SW', 368),
 ('N715SW', 397),
 ('N753SW', 226),
 ('N765SW', 226),
 ('N737JW', 1984),
 ('N780SW', 677),
 ('N749SW', 1797),
 ('N708SA', 1797),
 ('N768SW', 236),
 ('N758SW', 236),
 ('N742SW', 1363),
 ('N730SW', 1750),
 ('N724SW', 1750),
 ('N732SW', 1750),
 ('N752SW', 337),
 ('N720WN', 337),
 ('N735SA', 370),
 ('N718SW', 370),
 ('N792SW', 370),
 ('N746SW', 370),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N740SW', 308),
 ('N731SA', 308),
 ('N740SW', 308),
 ('N773SA', 308),
 ('N727SW', 373),
 ('N783SW', 289),
 ('N736SA', 293),
 ('N787SA', 393),
 ('N742SW', 451),
 ('N742SW', 1140),
 ('N730SW', 1363),
 ('N756SA', 1072),
 ('N713SW', 405),
 ('N728SW', 1044),
 ('N775SW', 1044),
 ('N768SW', 237),
 ('N704SW', 223),
 ('N706SW', 616),
 ('N785SW', 616),
 ('N713SW', 787),
 ('N789SW', 895),
 ('N736SA', 178),
 ('N778SW', 178),
 ('N752SW', 848),
 ('N786SW', 972),
 ('N709SW', 972),
 ('N779SW', 972),
 ('N780SW', 989),
 ('N766SW', 989),
 ('N739GB', 989),
 ('N743SW', 861),
 ('N785SW', 861),
 ('N705SW', 1073),
 ('N786SW', 1073),
 ('N786SW', 133),
 ('N707SA', 133),
 ('N795SW', 1040),
 ('N720WN', 880),
 ('N775SW', 880),
 ('N748SW', 1121),
 ('N709SW', 1121),
 ('N767SW', 972),
 ('N730SW', 777),
 ('N785SW', 468),
 ('N713SW', 468),
 ('N751SW', 611),
 ('N763SW', 611),
 ('N792SW', 611),
 ('N779SW', 307),
 ('N750SA', 284),
 ('N776WN', 284),
 ('N780SW', 895),
 ('N711HK', 895),
 ('N713SW', 229),
 ('N785SW', 229),
 ('N798SW', 1166),
 ('N717SA', 1166),
 ('N793SA', 937),
 ('N716SW', 937),
 ('N712SW', 577),
 ('N726SW', 162),
 ('N724SW', 765),
 ('N734SA', 765),
 ('N723SW', 1521),
 ('N753SW', 1521),
 ('N788SA', 1521),
 ('N765SW', 1521),
 ('N704SW', 405),
 ('N706SW', 989),
 ('N746SW', 989),
 ('N761RR', 838),
 ('N758SW', 1844),
 ('N739GB', 1844),
 ('N705SW', 1844),
 ('N754SW', 704),
 ('N766SW', 1751),
 ('N733SA', 668),
 ('N723SW', 1444),
 ('N732SW', 1444),
 ('N732SW', 402),
 ('N718SW', 1728),
 ('N729SW', 1728),
 ('N754SW', 1728),
 ('N764SW', 271),
 ('N725SW', 271),
 ('N761RR', 1855),
 ('N751SW', 1855),
 ('N750SA', 1258),
 ('N741SA', 251),
 ('N710SW', 997),
 ('N751SW', 997),
 ('N779SW', 1440),
 ('N713SW', 838),
 ('N761RR', 838),
 ('N771SA', 290),
 ('N790SW', 290),
 ('N757LV', 2279),
 ('N781WN', 321),
 ('N724SW', 303),
 ('N782SA', 1501),
 ('N711HK', 487),
 ('N727SW', 889),
 ('N774SW', 1959),
 ('N771SA', 325),
 ('N705SW', 325),
 ('N708SA', 325),
 ('N720WN', 957),
 ('N777QC', 723),
 ('N700GS', 1642),
 ('N799SW', 407),
 ('N787SA', 407),
 ('N788SA', 407),
 ('N766SW', 407),
 ('N784SW', 407),
 ('N787SA', 407),
 ('N740SW', 337),
 ('N708SA', 337),
 ('N780SW', 337),
 ('N733SA', 1844),
 ('N795SW', 361),
 ('N752SW', 180),
 ('N706SW', 180),
 ('N764SW', 446),
 ('N773SA', 446),
 ('N795SW', 446),
 ('N782SA', 588),
 ('N769SW', 588),
 ('N739GB', 588),
 ('N771SA', 371),
 ('N758SW', 371),
 ('N744SW', 747),
 ('N728SW', 313),
 ('N744SW', 833),
 ('N797MX', 1037),
 ('N740SW', 325),
 ('N773SA', 325),
 ('N742SW', 333),
 ('N788SA', 333),
 ('N795SW', 389),
 ('N737JW', 389),
 ('N791SW', 543),
 ('N785SW', 655)

### Efficient query

In [11]:
%%time
%%sql

SELECT TailNum, Distance
FROM flights
WHERE TailNum LIKE 'N7%'
LIMIT 2500;

 * sqlite:///flights.db
Done.
Wall time: 35 ms


[('N712SW', 810),
 ('N772SW', 810),
 ('N726SW', 688),
 ('N763SW', 1591),
 ('N765SW', 162),
 ('N778SW', 1489),
 ('N724SW', 220),
 ('N786SW', 220),
 ('N714CB', 220),
 ('N712SW', 2283),
 ('N798SW', 972),
 ('N736SA', 972),
 ('N795SW', 972),
 ('N707SA', 972),
 ('N753SW', 765),
 ('N779SW', 765),
 ('N704SW', 765),
 ('N709SW', 765),
 ('N792SW', 359),
 ('N714CB', 663),
 ('N726SW', 318),
 ('N791SW', 180),
 ('N799SW', 487),
 ('N777QC', 223),
 ('N784SW', 2106),
 ('N761RR', 1591),
 ('N792SW', 236),
 ('N787SA', 1295),
 ('N763SW', 1140),
 ('N775SW', 1140),
 ('N764SW', 1521),
 ('N723SW', 1521),
 ('N712SW', 1521),
 ('N725SW', 1521),
 ('N745SW', 1521),
 ('N740SW', 1521),
 ('N782SA', 407),
 ('N784SW', 407),
 ('N774SW', 407),
 ('N788SA', 197),
 ('N742SW', 197),
 ('N747SA', 256),
 ('N777QC', 256),
 ('N752SW', 256),
 ('N790SW', 256),
 ('N794SW', 1910),
 ('N715SW', 1910),
 ('N734SA', 258),
 ('N794SW', 1069),
 ('N768SW', 1624),
 ('N731SA', 866),
 ('N776WN', 386),
 ('N756SA', 368),
 ('N766SW', 368),
 ('N715SW', 397),
 ('N753SW', 226),
 ('N765SW', 226),
 ('N737JW', 1984),
 ('N780SW', 677),
 ('N749SW', 1797),
 ('N708SA', 1797),
 ('N768SW', 236),
 ('N758SW', 236),
 ('N742SW', 1363),
 ('N730SW', 1750),
 ('N724SW', 1750),
 ('N732SW', 1750),
 ('N752SW', 337),
 ('N720WN', 337),
 ('N735SA', 370),
 ('N718SW', 370),
 ('N792SW', 370),
 ('N746SW', 370),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N738CB', 337),
 ('N740SW', 308),
 ('N731SA', 308),
 ('N740SW', 308),
 ('N773SA', 308),
 ('N727SW', 373),
 ('N783SW', 289),
 ('N736SA', 293),
 ('N787SA', 393),
 ('N742SW', 451),
 ('N742SW', 1140),
 ('N730SW', 1363),
 ('N756SA', 1072),
 ('N713SW', 405),
 ('N728SW', 1044),
 ('N775SW', 1044),
 ('N768SW', 237),
 ('N704SW', 223),
 ('N706SW', 616),
 ('N785SW', 616),
 ('N713SW', 787),
 ('N789SW', 895),
 ('N736SA', 178),
 ('N778SW', 178),
 ('N752SW', 848),
 ('N786SW', 972),
 ('N709SW', 972),
 ('N779SW', 972),
 ('N780SW', 989),
 ('N766SW', 989),
 ('N739GB', 989),
 ('N743SW', 861),
 ('N785SW', 861),
 ('N705SW', 1073),
 ('N786SW', 1073),
 ('N786SW', 133),
 ('N707SA', 133),
 ('N795SW', 1040),
 ('N720WN', 880),
 ('N775SW', 880),
 ('N748SW', 1121),
 ('N709SW', 1121),
 ('N767SW', 972),
 ('N730SW', 777),
 ('N785SW', 468),
 ('N713SW', 468),
 ('N751SW', 611),
 ('N763SW', 611),
 ('N792SW', 611),
 ('N779SW', 307),
 ('N750SA', 284),
 ('N776WN', 284),
 ('N780SW', 895),
 ('N711HK', 895),
 ('N713SW', 229),
 ('N785SW', 229),
 ('N798SW', 1166),
 ('N717SA', 1166),
 ('N793SA', 937),
 ('N716SW', 937),
 ('N712SW', 577),
 ('N726SW', 162),
 ('N724SW', 765),
 ('N734SA', 765),
 ('N723SW', 1521),
 ('N753SW', 1521),
 ('N788SA', 1521),
 ('N765SW', 1521),
 ('N704SW', 405),
 ('N706SW', 989),
 ('N746SW', 989),
 ('N761RR', 838),
 ('N758SW', 1844),
 ('N739GB', 1844),
 ('N705SW', 1844),
 ('N754SW', 704),
 ('N766SW', 1751),
 ('N733SA', 668),
 ('N723SW', 1444),
 ('N732SW', 1444),
 ('N732SW', 402),
 ('N718SW', 1728),
 ('N729SW', 1728),
 ('N754SW', 1728),
 ('N764SW', 271),
 ('N725SW', 271),
 ('N761RR', 1855),
 ('N751SW', 1855),
 ('N750SA', 1258),
 ('N741SA', 251),
 ('N710SW', 997),
 ('N751SW', 997),
 ('N779SW', 1440),
 ('N713SW', 838),
 ('N761RR', 838),
 ('N771SA', 290),
 ('N790SW', 290),
 ('N757LV', 2279),
 ('N781WN', 321),
 ('N724SW', 303),
 ('N782SA', 1501),
 ('N711HK', 487),
 ('N727SW', 889),
 ('N774SW', 1959),
 ('N771SA', 325),
 ('N705SW', 325),
 ('N708SA', 325),
 ('N720WN', 957),
 ('N777QC', 723),
 ('N700GS', 1642),
 ('N799SW', 407),
 ('N787SA', 407),
 ('N788SA', 407),
 ('N766SW', 407),
 ('N784SW', 407),
 ('N787SA', 407),
 ('N740SW', 337),
 ('N708SA', 337),
 ('N780SW', 337),
 ('N733SA', 1844),
 ('N795SW', 361),
 ('N752SW', 180),
 ('N706SW', 180),
 ('N764SW', 446),
 ('N773SA', 446),
 ('N795SW', 446),
 ('N782SA', 588),
 ('N769SW', 588),
 ('N739GB', 588),
 ('N771SA', 371),
 ('N758SW', 371),
 ('N744SW', 747),
 ('N728SW', 313),
 ('N744SW', 833),
 ('N797MX', 1037),
 ('N740SW', 325),
 ('N773SA', 325),
 ('N742SW', 333),
 ('N788SA', 333),
 ('N795SW', 389),
 ('N737JW', 389),
 ('N791SW', 543),
 ('N785SW', 655)

### Why it’s more efficient
Using a wildcard at the beginning of a pattern will cause a full table scan. If you need to search for text at the beginning of a field, only use a trailing wildcard. This will take advantage of any indexing that is in place.

## Avoid using functions in predicates
**Scenario:** We want to return the origin and departure delay of all flights from a specific origin. 
 
### Inefficient query

In [12]:
%%time
%%sql

SELECT Origin, DepDelay 
FROM flights
WHERE LOWER(Origin) = 'las'
LIMIT 7000;

 * sqlite:///flights.db
Done.
Wall time: 360 ms


[('LAS', 53.0),
 ('LAS', -2.0),
 ('LAS', 83.0),
 ('LAS', 57.0),
 ('LAS', -1.0),
 ('LAS', 14.0),
 ('LAS', 2.0),
 ('LAS', 97.0),
 ('LAS', 34.0),
 ('LAS', 16.0),
 ('LAS', 63.0),
 ('LAS', 15.0),
 ('LAS', 59.0),
 ('LAS', 1.0),
 ('LAS', 1.0),
 ('LAS', 45.0),
 ('LAS', 26.0),
 ('LAS', 69.0),
 ('LAS', 4.0),
 ('LAS', 36.0),
 ('LAS', 69.0),
 ('LAS', 1.0),
 ('LAS', 63.0),
 ('LAS', 38.0),
 ('LAS', 0.0),
 ('LAS', 51.0),
 ('LAS', 211.0),
 ('LAS', 14.0),
 ('LAS', 10.0),
 ('LAS', 16.0),
 ('LAS', 56.0),
 ('LAS', 0.0),
 ('LAS', 9.0),
 ('LAS', 4.0),
 ('LAS', 23.0),
 ('LAS', 47.0),
 ('LAS', 3.0),
 ('LAS', 11.0),
 ('LAS', 69.0),
 ('LAS', 10.0),
 ('LAS', 1.0),
 ('LAS', 17.0),
 ('LAS', 77.0),
 ('LAS', 117.0),
 ('LAS', 30.0),
 ('LAS', 14.0),
 ('LAS', 27.0),
 ('LAS', 35.0),
 ('LAS', 9.0),
 ('LAS', 27.0),
 ('LAS', 65.0),
 ('LAS', 49.0),
 ('LAS', 10.0),
 ('LAS', 9.0),
 ('LAS', 41.0),
 ('LAS', 30.0),
 ('LAS', 275.0),
 ('LAS', 39.0),
 ('LAS', 52.0),
 ('LAS', 23.0),
 ('LAS', 17.0),
 ('LAS', 26.0),
 ('LAS', 16.0),
 ('LAS', 61.0),
 ('LAS', 4.0),
 ('LAS', 0.0),
 ('LAS', 15.0),
 ('LAS', 0.0),
 ('LAS', 28.0),
 ('LAS', 42.0),
 ('LAS', 38.0),
 ('LAS', 3.0),
 ('LAS', 3.0),
 ('LAS', 47.0),
 ('LAS', 9.0),
 ('LAS', 30.0),
 ('LAS', 16.0),
 ('LAS', 73.0),
 ('LAS', 58.0),
 ('LAS', 72.0),
 ('LAS', -2.0),
 ('LAS', 23.0),
 ('LAS', 19.0),
 ('LAS', 6.0),
 ('LAS', 3.0),
 ('LAS', 2.0),
 ('LAS', 9.0),
 ('LAS', 26.0),
 ('LAS', 19.0),
 ('LAS', -1.0),
 ('LAS', 8.0),
 ('LAS', 34.0),
 ('LAS', 90.0),
 ('LAS', 87.0),
 ('LAS', 44.0),
 ('LAS', 18.0),
 ('LAS', 0.0),
 ('LAS', 38.0),
 ('LAS', -2.0),
 ('LAS', None),
 ('LAS', 9.0),
 ('LAS', 124.0),
 ('LAS', 46.0),
 ('LAS', 43.0),
 ('LAS', 1.0),
 ('LAS', 51.0),
 ('LAS', 70.0),
 ('LAS', 13.0),
 ('LAS', 10.0),
 ('LAS', 1.0),
 ('LAS', 15.0),
 ('LAS', 2.0),
 ('LAS', 7.0),
 ('LAS', 80.0),
 ('LAS', 89.0),
 ('LAS', 3.0),
 ('LAS', 3.0),
 ('LAS', 30.0),
 ('LAS', 0.0),
 ('LAS', 3.0),
 ('LAS', 32.0),
 ('LAS', 58.0),
 ('LAS', 16.0),
 ('LAS', 15.0),
 ('LAS', 38.0),
 ('LAS', 28.0),
 ('LAS', 62.0),
 ('LAS', 21.0),
 ('LAS', 0.0),
 ('LAS', 33.0),
 ('LAS', 54.0),
 ('LAS', 42.0),
 ('LAS', 20.0),
 ('LAS', -1.0),
 ('LAS', 7.0),
 ('LAS', 7.0),
 ('LAS', 7.0),
 ('LAS', 27.0),
 ('LAS', 87.0),
 ('LAS', 1.0),
 ('LAS', 24.0),
 ('LAS', -2.0),
 ('LAS', -5.0),
 ('LAS', 46.0),
 ('LAS', 60.0),
 ('LAS', -4.0),
 ('LAS', 31.0),
 ('LAS', 75.0),
 ('LAS', 27.0),
 ('LAS', 11.0),
 ('LAS', -2.0),
 ('LAS', 40.0),
 ('LAS', 12.0),
 ('LAS', 30.0),
 ('LAS', 16.0),
 ('LAS', 59.0),
 ('LAS', 46.0),
 ('LAS', 33.0),
 ('LAS', -1.0),
 ('LAS', 11.0),
 ('LAS', 29.0),
 ('LAS', 33.0),
 ('LAS', 15.0),
 ('LAS', 57.0),
 ('LAS', -1.0),
 ('LAS', 40.0),
 ('LAS', 18.0),
 ('LAS', 25.0),
 ('LAS', -2.0),
 ('LAS', 18.0),
 ('LAS', 1.0),
 ('LAS', 50.0),
 ('LAS', 0.0),
 ('LAS', 18.0),
 ('LAS', 6.0),
 ('LAS', 10.0),
 ('LAS', 59.0),
 ('LAS', 42.0),
 ('LAS', 38.0),
 ('LAS', 58.0),
 ('LAS', 53.0),
 ('LAS', -3.0),
 ('LAS', 8.0),
 ('LAS', 11.0),
 ('LAS', 47.0),
 ('LAS', 9.0),
 ('LAS', 3.0),
 ('LAS', 21.0),
 ('LAS', 19.0),
 ('LAS', 12.0),
 ('LAS', -1.0),
 ('LAS', 27.0),
 ('LAS', 31.0),
 ('LAS', 59.0),
 ('LAS', 201.0),
 ('LAS', 80.0),
 ('LAS', -2.0),
 ('LAS', 116.0),
 ('LAS', 183.0),
 ('LAS', 32.0),
 ('LAS', 5.0),
 ('LAS', 32.0),
 ('LAS', 0.0),
 ('LAS', 34.0),
 ('LAS', 45.0),
 ('LAS', -4.0),
 ('LAS', 1.0),
 ('LAS', 39.0),
 ('LAS', 39.0),
 ('LAS', 119.0),
 ('LAS', 49.0),
 ('LAS', 23.0),
 ('LAS', 77.0),
 ('LAS', 24.0),
 ('LAS', 62.0),
 ('LAS', -4.0),
 ('LAS', 39.0),
 ('LAS', 19.0),
 ('LAS', -3.0),
 ('LAS', 51.0),
 ('LAS', 11.0),
 ('LAS', 19.0),
 ('LAS', 12.0),
 ('LAS', 15.0),
 ('LAS', -1.0),
 ('LAS', 0.0),
 ('LAS', 57.0),
 ('LAS', 75.0),
 ('LAS', 5.0),
 ('LAS', -3.0),
 ('LAS', 53.0),
 ('LAS', 28.0),
 ('LAS', 45.0),
 ('LAS', 55.0),
 ('LAS', 68.0),
 ('LAS', 56.0),
 ('LAS', 56.0),
 ('LAS', -5.0),
 ('LAS', 21.0),
 ('LAS', 38.0),
 ('LAS', 28.0),
 ('LAS', 10.0),
 ('LAS', -6.0),
 ('LAS', 51.0),
 ('LAS', 62.0),
 ('LAS', -2.0),
 ('LAS', 43.0),
 ('LAS', 57.0),
 ('LAS', 82.0),
 ('LAS', 13.0),
 ('LAS', 50.0),
 ('LAS', 91.0),
 ('LAS', -

### Efficient query

In [13]:
%%time
%%sql

WITH CTE AS
(SELECT LOWER(Origin) Origin_lower, DepDelay FROM flights)

SELECT * FROM CTE WHERE Origin_lower = 'las'
LIMIT 7000;

 * sqlite:///flights.db
Done.
Wall time: 430 ms


[('las', 53.0),
 ('las', -2.0),
 ('las', 83.0),
 ('las', 57.0),
 ('las', -1.0),
 ('las', 14.0),
 ('las', 2.0),
 ('las', 97.0),
 ('las', 34.0),
 ('las', 16.0),
 ('las', 63.0),
 ('las', 15.0),
 ('las', 59.0),
 ('las', 1.0),
 ('las', 1.0),
 ('las', 45.0),
 ('las', 26.0),
 ('las', 69.0),
 ('las', 4.0),
 ('las', 36.0),
 ('las', 69.0),
 ('las', 1.0),
 ('las', 63.0),
 ('las', 38.0),
 ('las', 0.0),
 ('las', 51.0),
 ('las', 211.0),
 ('las', 14.0),
 ('las', 10.0),
 ('las', 16.0),
 ('las', 56.0),
 ('las', 0.0),
 ('las', 9.0),
 ('las', 4.0),
 ('las', 23.0),
 ('las', 47.0),
 ('las', 3.0),
 ('las', 11.0),
 ('las', 69.0),
 ('las', 10.0),
 ('las', 1.0),
 ('las', 17.0),
 ('las', 77.0),
 ('las', 117.0),
 ('las', 30.0),
 ('las', 14.0),
 ('las', 27.0),
 ('las', 35.0),
 ('las', 9.0),
 ('las', 27.0),
 ('las', 65.0),
 ('las', 49.0),
 ('las', 10.0),
 ('las', 9.0),
 ('las', 41.0),
 ('las', 30.0),
 ('las', 275.0),
 ('las', 39.0),
 ('las', 52.0),
 ('las', 23.0),
 ('las', 17.0),
 ('las', 26.0),
 ('las', 16.0),
 ('las', 61.0),
 ('las', 4.0),
 ('las', 0.0),
 ('las', 15.0),
 ('las', 0.0),
 ('las', 28.0),
 ('las', 42.0),
 ('las', 38.0),
 ('las', 3.0),
 ('las', 3.0),
 ('las', 47.0),
 ('las', 9.0),
 ('las', 30.0),
 ('las', 16.0),
 ('las', 73.0),
 ('las', 58.0),
 ('las', 72.0),
 ('las', -2.0),
 ('las', 23.0),
 ('las', 19.0),
 ('las', 6.0),
 ('las', 3.0),
 ('las', 2.0),
 ('las', 9.0),
 ('las', 26.0),
 ('las', 19.0),
 ('las', -1.0),
 ('las', 8.0),
 ('las', 34.0),
 ('las', 90.0),
 ('las', 87.0),
 ('las', 44.0),
 ('las', 18.0),
 ('las', 0.0),
 ('las', 38.0),
 ('las', -2.0),
 ('las', None),
 ('las', 9.0),
 ('las', 124.0),
 ('las', 46.0),
 ('las', 43.0),
 ('las', 1.0),
 ('las', 51.0),
 ('las', 70.0),
 ('las', 13.0),
 ('las', 10.0),
 ('las', 1.0),
 ('las', 15.0),
 ('las', 2.0),
 ('las', 7.0),
 ('las', 80.0),
 ('las', 89.0),
 ('las', 3.0),
 ('las', 3.0),
 ('las', 30.0),
 ('las', 0.0),
 ('las', 3.0),
 ('las', 32.0),
 ('las', 58.0),
 ('las', 16.0),
 ('las', 15.0),
 ('las', 38.0),
 ('las', 28.0),
 ('las', 62.0),
 ('las', 21.0),
 ('las', 0.0),
 ('las', 33.0),
 ('las', 54.0),
 ('las', 42.0),
 ('las', 20.0),
 ('las', -1.0),
 ('las', 7.0),
 ('las', 7.0),
 ('las', 7.0),
 ('las', 27.0),
 ('las', 87.0),
 ('las', 1.0),
 ('las', 24.0),
 ('las', -2.0),
 ('las', -5.0),
 ('las', 46.0),
 ('las', 60.0),
 ('las', -4.0),
 ('las', 31.0),
 ('las', 75.0),
 ('las', 27.0),
 ('las', 11.0),
 ('las', -2.0),
 ('las', 40.0),
 ('las', 12.0),
 ('las', 30.0),
 ('las', 16.0),
 ('las', 59.0),
 ('las', 46.0),
 ('las', 33.0),
 ('las', -1.0),
 ('las', 11.0),
 ('las', 29.0),
 ('las', 33.0),
 ('las', 15.0),
 ('las', 57.0),
 ('las', -1.0),
 ('las', 40.0),
 ('las', 18.0),
 ('las', 25.0),
 ('las', -2.0),
 ('las', 18.0),
 ('las', 1.0),
 ('las', 50.0),
 ('las', 0.0),
 ('las', 18.0),
 ('las', 6.0),
 ('las', 10.0),
 ('las', 59.0),
 ('las', 42.0),
 ('las', 38.0),
 ('las', 58.0),
 ('las', 53.0),
 ('las', -3.0),
 ('las', 8.0),
 ('las', 11.0),
 ('las', 47.0),
 ('las', 9.0),
 ('las', 3.0),
 ('las', 21.0),
 ('las', 19.0),
 ('las', 12.0),
 ('las', -1.0),
 ('las', 27.0),
 ('las', 31.0),
 ('las', 59.0),
 ('las', 201.0),
 ('las', 80.0),
 ('las', -2.0),
 ('las', 116.0),
 ('las', 183.0),
 ('las', 32.0),
 ('las', 5.0),
 ('las', 32.0),
 ('las', 0.0),
 ('las', 34.0),
 ('las', 45.0),
 ('las', -4.0),
 ('las', 1.0),
 ('las', 39.0),
 ('las', 39.0),
 ('las', 119.0),
 ('las', 49.0),
 ('las', 23.0),
 ('las', 77.0),
 ('las', 24.0),
 ('las', 62.0),
 ('las', -4.0),
 ('las', 39.0),
 ('las', 19.0),
 ('las', -3.0),
 ('las', 51.0),
 ('las', 11.0),
 ('las', 19.0),
 ('las', 12.0),
 ('las', 15.0),
 ('las', -1.0),
 ('las', 0.0),
 ('las', 57.0),
 ('las', 75.0),
 ('las', 5.0),
 ('las', -3.0),
 ('las', 53.0),
 ('las', 28.0),
 ('las', 45.0),
 ('las', 55.0),
 ('las', 68.0),
 ('las', 56.0),
 ('las', 56.0),
 ('las', -5.0),
 ('las', 21.0),
 ('las', 38.0),
 ('las', 28.0),
 ('las', 10.0),
 ('las', -6.0),
 ('las', 51.0),
 ('las', 62.0),
 ('las', -2.0),
 ('las', 43.0),
 ('las', 57.0),
 ('las', 82.0),
 ('las', 13.0),
 ('las', 50.0),
 ('las', 91.0),
 ('las', -

### Why it’s more efficient
If we use functions in predicates, the index-based optimisations can’t be used. One alternative method is to use CTE’s instead.

## Avoid using calculated fields in the JOIN and WHERE clauses

**Scenario:** We want to return the flights where the departure delay was more than 20% of the flight time. 
 
### Inefficient query

In [14]:
%%time
%%sql

SELECT TailNum, DepDelay
FROM flights
WHERE AirTime/5 < DepDelay
LIMIT 5000;

 * sqlite:///flights.db
Done.
Wall time: 111 ms


[('N464WN', 34.0),
 ('N726SW', 25.0),
 ('N763SW', 67.0),
 ('N334SW', 94.0),
 ('N263WN', 9.0),
 ('N674AA', 28.0),
 ('N643SW', 51.0),
 ('N724SW', 32.0),
 ('N786SW', 20.0),
 ('N394SW', 25.0),
 ('N215WN', 87.0),
 ('N798SW', 82.0),
 ('N443WN', 39.0),
 ('N779SW', 82.0),
 ('N709SW', 29.0),
 ('N459WN', 56.0),
 ('N792SW', 315.0),
 ('N252WN', 45.0),
 ('N346SW', 53.0),
 ('N487WN', 23.0),
 ('N243WN', 26.0),
 ('N479WN', 30.0),
 ('N643SW', 38.0),
 ('N521SW', 44.0),
 ('N376SW', 8.0),
 ('N791SW', 58.0),
 ('N392SW', 9.0),
 ('N799SW', 53.0),
 ('N618WN', 83.0),
 ('N682SW', 57.0),
 ('N509SW', 14.0),
 ('N473WN', 97.0),
 ('N351SW', 34.0),
 ('N499WN', 63.0),
 ('N245WN', 59.0),
 ('N275WN', 45.0),
 ('N434WN', 69.0),
 ('N619SW', 36.0),
 ('N290WN', 69.0),
 ('N383SW', 63.0),
 ('N608SW', 38.0),
 ('N626SW', 51.0),
 ('N369SW', 211.0),
 ('N396SW', 14.0),
 ('N293', 10.0),
 ('N509SW', 16.0),
 ('N409WN', 56.0),
 ('N784SW', 47.0),
 ('N455WN', 69.0),
 ('N481WN', 17.0),
 ('N203WN', 77.0),
 ('N491WN', 117.0),
 ('N480WN', 30.0),
 ('N647SW', 27.0),
 ('N313SW', 35.0),
 ('N321SW', 27.0),
 ('N660SW', 65.0),
 ('N414WN', 49.0),
 ('N321SW', 41.0),
 ('N761RR', 275.0),
 ('N464WN', 39.0),
 ('N499WN', 23.0),
 ('N244WN', 17.0),
 ('N335SW', 26.0),
 ('N488WN', 16.0),
 ('N496WN', 61.0),
 ('N422WN', 15.0),
 ('N792SW', 28.0),
 ('N352SW', 42.0),
 ('N335SW', 38.0),
 ('N404WN', 47.0),
 ('N617SW', 30.0),
 ('N763SW', 73.0),
 ('N676SW', 58.0),
 ('N775SW', 72.0),
 ('N405WN', 90.0),
 ('N468WN', 87.0),
 ('N201LV', 44.0),
 ('N282WN', 38.0),
 ('N223WN', 124.0),
 ('N281WN', 46.0),
 ('N460WN', 43.0),
 ('N679AA', 51.0),
 ('N378SW', 70.0),
 ('N622SW', 80.0),
 ('N217JC', 89.0),
 ('N259WN', 30.0),
 ('N301SW', 32.0),
 ('N356SW', 58.0),
 ('N742SW', 16.0),
 ('N313SW', 15.0),
 ('N273WN', 38.0),
 ('N660SW', 28.0),
 ('N466WN', 62.0),
 ('N258WN', 33.0),
 ('N608SW', 54.0),
 ('N603SW', 27.0),
 ('N221WN', 87.0),
 ('N378SW', 24.0),
 ('N258WN', 46.0),
 ('N281WN', 60.0),
 ('N777QC', 31.0),
 ('N752SW', 75.0),
 ('N487WN', 27.0),
 ('N790SW', 11.0),
 ('N403WN', 59.0),
 ('N267WN', 46.0),
 ('N450WN', 33.0),
 ('N428WN', 29.0),
 ('N400WN', 33.0),
 ('N442WN', 15.0),
 ('N286WN', 57.0),
 ('N466WN', 40.0),
 ('N487WN', 18.0),
 ('N610WN', 25.0),
 ('N315SW', 18.0),
 ('N692SW', 50.0),
 ('N902WN', 18.0),
 ('N490WN', 10.0),
 ('N692SW', 59.0),
 ('N646SW', 42.0),
 ('N414WN', 38.0),
 ('N405WN', 58.0),
 ('N454WN', 53.0),
 ('N902WN', 47.0),
 ('N431WN', 27.0),
 ('N615SW', 31.0),
 ('N491WN', 59.0),
 ('N302SW', 201.0),
 ('N602SW', 80.0),
 ('N447WN', 116.0),
 ('N492WN', 183.0),
 ('N361SW', 32.0),
 ('N429WN', 32.0),
 ('N437WN', 34.0),
 ('N306SW', 45.0),
 ('N446WN', 39.0),
 ('N455WN', 39.0),
 ('N395SW', 119.0),
 ('N756SA', 49.0),
 ('N351SW', 23.0),
 ('N766SW', 77.0),
 ('N613SW', 24.0),
 ('N385SW', 62.0),
 ('N715SW', 39.0),
 ('N324SW', 19.0),
 ('N626SW', 51.0),
 ('N445WN', 19.0),
 ('N640SW', 15.0),
 ('N264LV', 57.0),
 ('N765SW', 75.0),
 ('N472WN', 53.0),
 ('N600WN', 45.0),
 ('N737JW', 55.0),
 ('N314SW', 68.0),
 ('N264LV', 56.0),
 ('N342SW', 56.0),
 ('N267WN', 21.0),
 ('N446WN', 38.0),
 ('N489WN', 28.0),
 ('N364SW', 25.0),
 ('N690SW', 40.0),
 ('N708SA', 52.0),
 ('N684WN', 110.0),
 ('N335SW', 20.0),
 ('N496WN', 77.0),
 ('N667SW', 45.0),
 ('N401WN', 36.0),
 ('N622SW', 30.0),
 ('N768SW', 12.0),
 ('N314SW', 27.0),
 ('N676SW', 55.0),
 ('N351SW', 12.0),
 ('N499WN', 25.0),
 ('N758SW', 9.0),
 ('N352SW', 57.0),
 ('N335SW', 30.0),
 ('N272WN', 48.0),
 ('N632SW', 53.0),
 ('N550WN', 48.0),
 ('N473WN', 30.0),
 ('N683SW', 64.0),
 ('N631SW', 23.0),
 ('N268WN', 19.0),
 ('N752SW', 22.0),
 ('N720WN', 33.0),
 ('N342SW', 46.0),
 ('N648SW', 31.0),
 ('N476WN', 27.0),
 ('N224WN', 34.0),
 ('N489WN', 20.0),
 ('N422WN', 22.0),
 ('N304SW', 110.0),
 ('N361SW', 23.0),
 ('N269WN', 46.0),
 ('N229WN', 21.0),
 ('N718SW', 75.0),
 ('N342SW', 14.0),
 ('N283WN', 36.0),
 ('N637SW', 76.0),
 ('N202WN', 35.0),
 ('N288WN', 20.0),
 ('N792SW', 44.0),
 ('N283WN', 18.0),
 ('N618WN', 22.0),
 ('N901WN', 206.0),
 ('N738CB', 123.0),
 ('N738CB', 115.0),
 ('N738CB', 135.0),
 ('N901WN', 193.0),


### Efficient query

In [15]:
%%time
%%sql

WITH CTE AS 
(SELECT AirTime/5 as fifth_time, DepDelay, TailNum FROM flights)

SELECT TailNum, DepDelay 
FROM CTE
WHERE CTE.fifth_time < CTE.DepDelay
LIMIT 5000;

 * sqlite:///flights.db
Done.
Wall time: 44 ms


[('N464WN', 34.0),
 ('N726SW', 25.0),
 ('N763SW', 67.0),
 ('N334SW', 94.0),
 ('N263WN', 9.0),
 ('N674AA', 28.0),
 ('N643SW', 51.0),
 ('N724SW', 32.0),
 ('N786SW', 20.0),
 ('N394SW', 25.0),
 ('N215WN', 87.0),
 ('N798SW', 82.0),
 ('N443WN', 39.0),
 ('N779SW', 82.0),
 ('N709SW', 29.0),
 ('N459WN', 56.0),
 ('N792SW', 315.0),
 ('N252WN', 45.0),
 ('N346SW', 53.0),
 ('N487WN', 23.0),
 ('N243WN', 26.0),
 ('N479WN', 30.0),
 ('N643SW', 38.0),
 ('N521SW', 44.0),
 ('N376SW', 8.0),
 ('N791SW', 58.0),
 ('N392SW', 9.0),
 ('N799SW', 53.0),
 ('N618WN', 83.0),
 ('N682SW', 57.0),
 ('N509SW', 14.0),
 ('N473WN', 97.0),
 ('N351SW', 34.0),
 ('N499WN', 63.0),
 ('N245WN', 59.0),
 ('N275WN', 45.0),
 ('N434WN', 69.0),
 ('N619SW', 36.0),
 ('N290WN', 69.0),
 ('N383SW', 63.0),
 ('N608SW', 38.0),
 ('N626SW', 51.0),
 ('N369SW', 211.0),
 ('N396SW', 14.0),
 ('N293', 10.0),
 ('N509SW', 16.0),
 ('N409WN', 56.0),
 ('N784SW', 47.0),
 ('N455WN', 69.0),
 ('N481WN', 17.0),
 ('N203WN', 77.0),
 ('N491WN', 117.0),
 ('N480WN', 30.0),
 ('N647SW', 27.0),
 ('N313SW', 35.0),
 ('N321SW', 27.0),
 ('N660SW', 65.0),
 ('N414WN', 49.0),
 ('N321SW', 41.0),
 ('N761RR', 275.0),
 ('N464WN', 39.0),
 ('N499WN', 23.0),
 ('N244WN', 17.0),
 ('N335SW', 26.0),
 ('N488WN', 16.0),
 ('N496WN', 61.0),
 ('N422WN', 15.0),
 ('N792SW', 28.0),
 ('N352SW', 42.0),
 ('N335SW', 38.0),
 ('N404WN', 47.0),
 ('N617SW', 30.0),
 ('N763SW', 73.0),
 ('N676SW', 58.0),
 ('N775SW', 72.0),
 ('N405WN', 90.0),
 ('N468WN', 87.0),
 ('N201LV', 44.0),
 ('N282WN', 38.0),
 ('N223WN', 124.0),
 ('N281WN', 46.0),
 ('N460WN', 43.0),
 ('N679AA', 51.0),
 ('N378SW', 70.0),
 ('N622SW', 80.0),
 ('N217JC', 89.0),
 ('N259WN', 30.0),
 ('N301SW', 32.0),
 ('N356SW', 58.0),
 ('N742SW', 16.0),
 ('N313SW', 15.0),
 ('N273WN', 38.0),
 ('N660SW', 28.0),
 ('N466WN', 62.0),
 ('N258WN', 33.0),
 ('N608SW', 54.0),
 ('N603SW', 27.0),
 ('N221WN', 87.0),
 ('N378SW', 24.0),
 ('N258WN', 46.0),
 ('N281WN', 60.0),
 ('N777QC', 31.0),
 ('N752SW', 75.0),
 ('N487WN', 27.0),
 ('N790SW', 11.0),
 ('N403WN', 59.0),
 ('N267WN', 46.0),
 ('N450WN', 33.0),
 ('N428WN', 29.0),
 ('N400WN', 33.0),
 ('N442WN', 15.0),
 ('N286WN', 57.0),
 ('N466WN', 40.0),
 ('N487WN', 18.0),
 ('N610WN', 25.0),
 ('N315SW', 18.0),
 ('N692SW', 50.0),
 ('N902WN', 18.0),
 ('N490WN', 10.0),
 ('N692SW', 59.0),
 ('N646SW', 42.0),
 ('N414WN', 38.0),
 ('N405WN', 58.0),
 ('N454WN', 53.0),
 ('N902WN', 47.0),
 ('N431WN', 27.0),
 ('N615SW', 31.0),
 ('N491WN', 59.0),
 ('N302SW', 201.0),
 ('N602SW', 80.0),
 ('N447WN', 116.0),
 ('N492WN', 183.0),
 ('N361SW', 32.0),
 ('N429WN', 32.0),
 ('N437WN', 34.0),
 ('N306SW', 45.0),
 ('N446WN', 39.0),
 ('N455WN', 39.0),
 ('N395SW', 119.0),
 ('N756SA', 49.0),
 ('N351SW', 23.0),
 ('N766SW', 77.0),
 ('N613SW', 24.0),
 ('N385SW', 62.0),
 ('N715SW', 39.0),
 ('N324SW', 19.0),
 ('N626SW', 51.0),
 ('N445WN', 19.0),
 ('N640SW', 15.0),
 ('N264LV', 57.0),
 ('N765SW', 75.0),
 ('N472WN', 53.0),
 ('N600WN', 45.0),
 ('N737JW', 55.0),
 ('N314SW', 68.0),
 ('N264LV', 56.0),
 ('N342SW', 56.0),
 ('N267WN', 21.0),
 ('N446WN', 38.0),
 ('N489WN', 28.0),
 ('N364SW', 25.0),
 ('N690SW', 40.0),
 ('N708SA', 52.0),
 ('N684WN', 110.0),
 ('N335SW', 20.0),
 ('N496WN', 77.0),
 ('N667SW', 45.0),
 ('N401WN', 36.0),
 ('N622SW', 30.0),
 ('N768SW', 12.0),
 ('N314SW', 27.0),
 ('N676SW', 55.0),
 ('N351SW', 12.0),
 ('N499WN', 25.0),
 ('N758SW', 9.0),
 ('N352SW', 57.0),
 ('N335SW', 30.0),
 ('N272WN', 48.0),
 ('N632SW', 53.0),
 ('N550WN', 48.0),
 ('N473WN', 30.0),
 ('N683SW', 64.0),
 ('N631SW', 23.0),
 ('N268WN', 19.0),
 ('N752SW', 22.0),
 ('N720WN', 33.0),
 ('N342SW', 46.0),
 ('N648SW', 31.0),
 ('N476WN', 27.0),
 ('N224WN', 34.0),
 ('N489WN', 20.0),
 ('N422WN', 22.0),
 ('N304SW', 110.0),
 ('N361SW', 23.0),
 ('N269WN', 46.0),
 ('N229WN', 21.0),
 ('N718SW', 75.0),
 ('N342SW', 14.0),
 ('N283WN', 36.0),
 ('N637SW', 76.0),
 ('N202WN', 35.0),
 ('N288WN', 20.0),
 ('N792SW', 44.0),
 ('N283WN', 18.0),
 ('N618WN', 22.0),
 ('N901WN', 206.0),
 ('N738CB', 123.0),
 ('N738CB', 115.0),
 ('N738CB', 135.0),
 ('N901WN', 193.0),


### Why it’s more efficient

Calculated fields in JOIN and WHERE clauses also prevent indices from being used. CTEs can be used instead here as well.


## Conclusion

In this train, we covered different strategies for optimising SQL queries. These can be summarised as follows:

- **Column names instead of ***
    - Taxing to return records of all columns for big tables
    - Limit amount of data being read by specifying subset of columns
    
    
- **Create JOINS with INNER, not WHERE**
    - WHERE clause does a CROSS join which considers the combination of rows from both tables
    - Join statements only iterate through records in the left table when looking for matches.
 
 
- **Avoid using the wildcard (%) at the beginning of a predicate**
    - Execution will be slower if % at beginning due to full table scan
    - Use only trailing wildcard when searching for start of word


- **Avoid using functions in predicates**
    - Execution will be slower, due to not using indices
    - Create CTE to handle it instead
     
    
- **Avoid using calculated fields in the JOIN and WHERE clauses**
    - Avoid Calculated Fields in JOIN and WHERE clause
    - Create CTE to handle it instead
    
As demonstrated in the train, another quick way to make queries more efficient, particularly in cases where we don't want the full output of a query, is to use the `LIMIT` keyword. 

## Appendix

The following links may be useful for further learning around the content we've covered: 

 - [SQL Server CTEs](https://www.sqlservertutorial.net/sql-server-basics/sql-server-cte/)
 - [8 ways to fine tune SQL queries](https://www.sisense.com/blog/8-ways-fine-tune-sql-queries-production-databases/)